In [2]:
import altair as alt
import boto3
import pandas as pd
import numpy as np
import os
from tqdm.notebook import tqdm

# Download data from S3
Download most recent death data from s3 into `deathdata.csv`. Skip if you've done this recently it's a big file :) 

In [72]:
session = boto3.Session(
    aws_access_key_id=os.environ["S3_KEY"],
    aws_secret_access_key=os.environ["S3_PRIVATE_KEY"]
)
s3 = session.client('s3')
from pprint import pprint
def hook(t):
  def inner(bytes_amount):
    t.update(bytes_amount)
  return inner

BUCKET_NAME = 'nvss-deaths'
file = sorted([el['Key'] for el in s3.list_objects(Bucket=BUCKET_NAME)['Contents']],reverse=True)[0]

path = "deathdata.csv"
file_object = s3.get_object(Bucket=BUCKET_NAME, Key=file)
filesize = file_object['ContentLength']

with tqdm(total=filesize, unit='B') as t:
    with open(path, 'wb') as f:
        s3.download_fileobj(BUCKET_NAME, file, f, Callback=hook(t))

  0%|          | 0/825973158 [00:00<?, ?B/s]

# Preprocessing
Read in data from `deathdata.csv` and do necessary preprocessing

In [3]:
# Read in the file
dtype = {
    'State' : 'string',
    'Indicator': 'string',
    'COVID-19 Deaths': 'float64',
    'Pneumonia Deaths': 'float64',
    'Pneumonia and COVID-19 Deaths': 'float64',
    'Influenza Deaths': 'float64',
    'Pneumonia, Influenza, or COVID-19 Deaths': 'float64',
    'Total Deaths': 'float64',
    'Percent of Expected Deaths': 'float64',
    'Start week': 'string',
    'End Week': 'string',
    'Start Date': 'string',
    'End Date': 'string',
    'MMWR Week': 'float64',
    'Week Ending Date': 'string',
    'Data as of': 'string'
}
deaths = pd.read_csv('deathdata.csv',dtype=dtype,low_memory=False).drop('Unnamed: 0',axis=1)
deaths

Unnamed: 0.1  Data as of  Start week    End Week    Group   
0                   0  05/22/2020  02/01/2020  02/01/2020  by week  \
1                   1  05/22/2020  02/08/2020  02/08/2020  by week   
2                   2  05/22/2020  02/15/2020  02/15/2020  by week   
3                   3  05/22/2020  02/22/2020  02/22/2020  by week   
4                   4  05/22/2020  02/29/2020  02/29/2020  by week   
...               ...         ...         ...         ...      ...   
4448334       4448334  07/06/2023        <NA>        <NA>  by week   
4448335       4448335  07/06/2023        <NA>        <NA>  by week   
4448336       4448336  07/06/2023        <NA>        <NA>  by week   
4448337       4448337  07/06/2023        <NA>        <NA>  by week   
4448338       4448338  07/06/2023        <NA>        <NA>  by week   

                 State    Indicator  COVID-19 Deaths  Total Deaths   
0        United States  Week-ending              0.0       57584.0  \
1        United States  Week-ending              1.0       58245.0   
2        United States  Week-ending              0.0       57585.0   
3        United States  Week-ending              2.0       57640.0   
4        United States  Week-ending              5.0       57956.0   
...                ...          ...              ...           ...   
4448334    Puerto Rico         <NA>             21.0         585.0   
4448335    Puerto Rico         <NA>             33.0         685.0   
4448336    Puerto Rico         <NA>             26.0         533.0   
4448337    Puerto Rico         <NA>             18.0         378.0   
4448338    Puerto Rico         <NA>             19.0         245.0   

         Percent of Expected Deaths  ...  Pneumonia and COVID-19 Deaths   
0                              0.97  ...                            0.0  \
1                              0.97  ...                            0.0   
2                              0.98  ...                            0.0   
3                              0.99  ...                            0.0   
4                              1.01  ...                            3.0   
...                             ...  ...                            ...   
4448334                      109.00  ...                           13.0   
4448335                      126.00  ...                           19.0   
4448336                       92.00  ...                           24.0   
4448337                       69.00  ...                           11.0   
4448338                       44.00  ...                           14.0   

         Influenza Deaths  Pneumonia, Influenza, or COVID-19 Deaths   
0                   475.0                                    4188.0  \
1                   507.0                                    4223.0   
2                   541.0                                    4288.0   
3                   553.0                                    4165.0   
4                   629.0                                    4358.0   
...                   ...                                       ...   
4448334               NaN                                     109.0   
4448335               NaN                                     116.0   
4448336               NaN                                      94.0   
4448337               NaN                                      86.0   
4448338               NaN                                      64.0   

                                                  Footnote  Start Date   
0                                                      NaN        <NA>  \
1                                                      NaN        <NA>   
2                                                      NaN        <NA>   
3                                                      NaN        <NA>   
4                                                      NaN        <NA>   
...                                                    ...         ...   
4448334  One or more data cells have counts between 1-9

In [4]:
# Change date cols to datetime
date_cols = ['Data as of','End Week','Week Ending Date']
for date_col in date_cols:
    deaths[date_col] = pd.to_datetime(deaths[date_col],errors='coerce')
    
# Merge week ending date and end week (changed field name)
deaths['Weekdate'] = deaths['Week Ending Date'].fillna(deaths['End Week'])

# Sort and drop all the irrelevant columns
deaths = deaths.sort_values(by=['State','Weekdate','Data as of'],ascending=[True,True,True])
deaths = deaths[['State','Weekdate','Data as of','COVID-19 Deaths','Total Deaths']]
deaths['Percent COVID Deaths'] = deaths['COVID-19 Deaths']/deaths['Total Deaths']

# Add map categories from https://covid.cdc.gov/covid-data-tracker/#cases_percent-covid-deaths
deaths['Map Category'] = np.select([
    deaths['Percent COVID Deaths'].isna(), # 0
    deaths['Percent COVID Deaths']< 0.02, # 1
    deaths['Percent COVID Deaths'].between(0.02,.04,inclusive='left'), # 2
    deaths['Percent COVID Deaths'].between(0.04,0.06,inclusive='left'), # 3
    deaths['Percent COVID Deaths'].between(0.06,0.08,inclusive='left'), # 4
    deaths['Percent COVID Deaths'] >= 0.08], # 5
    [0,1,2,3,4,5]
)
deaths

State   Weekdate Data as of  COVID-19 Deaths  Total Deaths   
274157   Alabama 2020-01-04 2021-01-06              0.0         630.0  \
277019   Alabama 2020-01-04 2021-01-07              0.0        1081.0   
279881   Alabama 2020-01-04 2021-01-08              0.0        1081.0   
282745   Alabama 2020-01-04 2021-01-11              0.0        1081.0   
285661   Alabama 2020-01-04 2021-01-12              0.0        1081.0   
...          ...        ...        ...              ...           ...   
4448154  Wyoming 2023-06-24 2023-07-06              0.0          57.0   
4418509  Wyoming 2023-07-01 2023-07-03              0.0           NaN   
4428391  Wyoming 2023-07-01 2023-07-03              0.0           NaN   
4438273  Wyoming 2023-07-01 2023-07-05              0.0          16.0   
4448155  Wyoming 2023-07-01 2023-07-06              0.0          16.0   

         Percent COVID Deaths  Map Category  
274157                    0.0             1  
277019                    0.0             1  
279881                    0.0             1  
282745                    0.0             1  
285661                    0.0             1  
...                       ...           ...  
4448154                   0.0             1  
4418509                   NaN             0  
4428391                   NaN             0  
4438273                   0.0             1  
4448155                   0.0             1  

[4448339 rows x 7 columns]

# Analysis
Look at overall and jurisdiction-level volatility in percent COVID-19 associated deaths

## Excluding Days of No Reporting

In [5]:
deaths_no_zero = deaths[deaths['Map Category']!=0]
deaths_agg = deaths_no_zero.groupby(['State','Weekdate']).agg({'Map Category' : ['mean','min','max','count'],
                                                       'Percent COVID Deaths' : ['mean','min','max']})

deaths_agg.columns=deaths_agg.columns.to_flat_index()
deaths_agg = deaths_agg.reset_index()
deaths_agg.columns = [str(c).translate({ord(c): None for c in '(),\''}) for c in deaths_agg.columns]
deaths_agg['cat_diff'] = deaths_agg['Map Category max']-deaths_agg['Map Category min']
deaths_agg['percent_diff'] = (deaths_agg['Percent COVID Deaths max']-deaths_agg['Percent COVID Deaths min'])*100
deaths_agg_agg = deaths_agg.groupby('State').agg({'cat_diff': ['mean','min','max'],'percent_diff': ['mean','min','max']})

deaths_agg_agg.columns = [str(c).strip('()').replace('\'','') for c in deaths_agg_agg.columns.to_flat_index()]
diffs = deaths_agg_agg.reset_index()['percent_diff, mean']
cat_diffs = deaths_agg_agg['cat_diff, mean']
print('Average difference in percent of deaths that are COVID-19 associated per state: ',np.mean(diffs),' with std ',np.std(diffs))
print('Average map category difference per state:', np.mean(cat_diffs),' with std ',np.std(cat_diffs))


Average difference in percent of deaths that are COVID-19 associated per state:  3.8585252476265572  with std  4.409716095792606
Average map category difference per state: 0.5294949946636679  with std  0.1786133780468748


In [15]:
alt.data_transformers.disable_max_rows()
alt.Chart(deaths_agg).mark_line().encode(
    x='month(Weekdate):T',
    y=alt.Y('mean(percent_diff):Q',title='Difference (max-min on date)'),
    color=alt.Color('year(Weekdate):N')
).properties(
    width=180,
    height=500
).facet(
    facet=alt.Row('State:N',title=None),
    columns=6
).properties(
    title="Difference in Percent Deaths that are COVID-19 Over Time By State (average per month)"
).configure_header(
    labelFontSize=13
).configure_title(
    fontSize=15,
    anchor='middle'
)

alt.FacetChart(...)

In [25]:
alt.data_transformers.disable_max_rows()
alt.Chart(deaths_agg[(deaths_agg['Weekdate']>'2023-01-01') & (deaths_agg['State'] != 'United States')]).mark_bar().encode(
    x='month(Weekdate):T',
    y=alt.Y('mean(percent_diff):Q',title='Difference (max-min on date)'),
    color=alt.Color('year(Weekdate):N')
).properties(
    width=180,
    height=180
).facet(
    facet=alt.Row('State:N',title=None),
    columns=7
).properties(
    title="Difference in Percent Deaths that are COVID-19 Over Time By State (average per month)"
).configure_header(
    labelFontSize=13
).configure_title(
    fontSize=15,
    anchor='middle'
)

alt.FacetChart(...)

In [167]:
# Statistics on missing data
deaths_agg = deaths.groupby(['State','Weekdate']).agg({'Map Category' : ['mean','min','max'],
                                                       'Percent COVID Deaths' : ['min','max']})
deaths_agg.columns = [str(c).strip('()').replace('\'','').replace(',','') for c in deaths_agg.columns.to_flat_index()]

deaths_agg = deaths_agg.reset_index()
missing_data = deaths_agg[(deaths_agg['Map Category min']==0) & (deaths_agg['Map Category max']-deaths_agg['Map Category min']>0)]
weeks_missing = missing_data.groupby('State').agg('count')['Weekdate']
weeks_total = deaths_agg.groupby('State').agg('count')['Weekdate']
print("Average days of missing data per state: ", np.mean(weeks_missing)," with std ", np.std(weeks_missing))
print("Total weeks of data: ",np.mean(weeks_total))

alt.

Average days of missing data per state:  106.67924528301887  with std  33.919868716874845
Total weeks of data:  213.0


State   Weekdate  Map Category mean  Map Category min   
3      Alabama 2020-01-25           0.125387                 0  \
12     Alabama 2020-02-29           0.234177                 0   
36     Alabama 2020-05-23           3.993663                 0   
46     Alabama 2020-06-27           4.961881                 0   
48     Alabama 2020-07-04           4.954198                 0   
...        ...        ...                ...               ...   
11497  Wyoming 2023-06-03           0.250000                 0   
11498  Wyoming 2023-06-10           0.880000                 0   
11499  Wyoming 2023-06-17           0.941176                 0   
11500  Wyoming 2023-06-24           0.909091                 0   
11501  Wyoming 2023-07-01           0.500000                 0   

       Map Category max  Percent COVID Deaths min  Percent COVID Deaths max  
3                     1                  0.000000                  0.000000  
12                    1                  0.000000                  0.000000  
36                    4                  0.055794                  0.071119  
46                    5                  0.027823                  0.090657  
48                    5                  0.023404                  0.104080  
...                 ...                       ...                       ...  
11497                 1                  0.000000                  0.000000  
11498                 1                  0.000000                  0.000000  
11499                 1                  0.000000                  0.000000  
11500                 1                  0.000000                  0.000000  
11501                 1                  0.000000                  0.000000  

[5654 rows x 7 columns]

alt.Chart(...)

In [140]:
deaths_agg.columns

Index(['State', 'Weekdate', 'Map Category mean', 'Map Category min',
       'Map Category max', 'Percent COVID Deaths min',
       'Percent COVID Deaths max'],
      dtype='object')